In [2]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - folium=0.5.0


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    ca-certificates-2020.4.5.1 |       hecc5488_0         146 KB  conda-forge
    branca-0.4.1               |             py_0          26 KB  conda-forge
    vincent-0.4.4              |             py_1          28 KB  conda-forge
    python_abi-3.6             |          1_cp36m           4 KB  conda-forge
    openssl-1.1.1g             |       h516909a_0         2.1 MB  conda-forge
    folium-0.5.0               |             py_0          45 KB  conda-forge
    certifi-2020.4.5.1         |   py36h9f0ad1d_0         151 KB  conda-forge
    altair-4.1.0               |             py_1         614 KB  conda-forge
    ------------------------------------------------------------
                       

In [3]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


## Load and explore the data

In [4]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [5]:
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

## all the relevant data is in the features key, which is basically a list of the neighborhoods

In [6]:
neighborhoods_data = newyork_data['features']

# Tranform the data into a pandas dataframe


In [7]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

### Then let's loop through the data and fill the dataframe one row at a time.



In [8]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [9]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [10]:
#neighborhoods.to_excel("C:\\Users\\Mirzana\\IBM\\toronto_grouped.xlsx", index = None, header=True, encoding = 'utf8-8')
#or

In [11]:
out_path = "C:\\Users\\Mirzana\\IBM\\NY_data.xlsx"

writer = pd.ExcelWriter(out_path , engine='xlsxwriter')
neighborhoods.to_excel(writer, sheet_name='Sheet1')
writer.save()

## Use geopy library to get the latitude and longitude values of New York City.


In [12]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


## Create a map of New York with neighborhoods superimposed on top.


In [14]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

## Define Foursquare Credentials and Version


In [18]:
CLIENT_ID = 'LWDSUY2O3RGJGCZO5T4JZZCD24KDKXOIXIICADYRSOJMBL3R' # your Foursquare ID
CLIENT_SECRET = 'AUDBVAMHY1ERTX3SJR4I0QXTYTCK33DVZBHIBKIDC1WDDA3R' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: LWDSUY2O3RGJGCZO5T4JZZCD24KDKXOIXIICADYRSOJMBL3R
CLIENT_SECRET:AUDBVAMHY1ERTX3SJR4I0QXTYTCK33DVZBHIBKIDC1WDDA3R


## Now, let's get the top 100 venues

In [19]:
LIMIT = 100 
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

## Now write the code to run the above function on each neighborhood and create a new dataframe called NY_venues

In [20]:
NY_venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

### Let's check the size of the resulting dataframe


In [21]:
print(NY_venues.shape)
NY_venues.head()

(9822, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop  
2         Walgreens       40.896528       -73.844700        Pharmacy  
3          Rite Aid       40.896649       -73.844846        Pharmacy  
4           Dunkin'       40.890459       -73.849089      Donut Shop

In [22]:
NY_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Allerton                                      25                      25   
Annadale                                      11                      11   
Arden Heights                                  4                       4   
Arlington                                      6                       6   
Arrochar                                      23                      23   
Arverne                                       18                      18   
Astoria                                       95                      95   
Astoria Heights                               13                      13   
Auburndale                                    16                      16   
Bath Beach                                    47                      47   
Battery Park City                             62                      62   
Bay Ridge                                     81                      81   
Bay Terrace                                   48                      48   
Baychester                                    20                      20   
Bayside                                       70                      70   
Bayswater                                      2                       2   
Bedford Park                                  34                      34   
Bedford Stuyvesant                            26                      26   
Beechhurst                                    14                      14   
Bellaire                                      13                      13   
Belle Harbor                                  17                      17   
Bellerose                                     22                      22   
Belmont                                      100                     100   
Bensonhurst                                   32                      32   
Bergen Beach                                   7                       7   
Blissville                                    15                      15   
Bloomfield                                     5                       5   
Boerum Hill                                   91                      91   
Borough Park                                  22                      22   
Breezy Point                                   3                       3   
Briarwood                                     11                      11   
Brighton Beach                                44                      44   
Broad Channel                                  5                       5   
Broadway Junction                             16                      16   
Bronxdale                                     14                      14   
Brooklyn Heights                             100                     100   
Brookville                                     1                       1   
Brownsville                                   17                      17   
Bulls Head                                    46                      46   
Bushwick                                      70                      70   
Butler Manor                                   7                       7   
Cambria Heights                               11                      11   
Canarsie                                       4                       4   
Carnegie Hill                                 85                      85   
Carroll Gardens                              100                     100   
Castle Hill                                    8                       8   
Castleton Corners                             17                      17   
Central Harlem                                46                      46   
Charleston                                    27                      27   
Chelsea                                      105                     105   
Chinatown                                    100                     100   

In [23]:
print('There are {} unique categories.'.format(len(NY_venues['Venue Category'].unique())))

There are 430 unique categories.


In [24]:
NY_onehot = pd.get_dummies(NY_venues[['Venue Category']], prefix = "", prefix_sep = "")

NY_onehot['Neighborhood'] = NY_venues['Neighborhood']

col_list = list(NY_onehot.columns)
col_list.remove('Neighborhood')
cols = ['Neighborhood'] + [col for col in col_list]

NY_onehot = NY_onehot[cols]

NY_onehot.head()

Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0    Wakefield                  0               0                  0   
1    Wakefield                  0               0                  0   
2    Wakefield                  0               0                  0   
3    Wakefield                  0               0                  0   
4    Wakefield                  0               0                  0   

   African Restaurant  American Restaurant  Animal Shelter  Antique Shop  \
0                   0                    0               0             0   
1                   0                    0               0             0   
2                   0                    0               0             0   
3                   0                    0               0             0   
4                   0                    0               0             0   

   Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0       0                 0                       0            0           0   
1       0                 0                       0            0           0   
2       0                 0                       0            0           0   
3       0                 0                       0            0           0   
4       0                 0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                   0           0                      0                    0   
1                   0           0                      0                    0   
2                   0           0                      0                    0   
3                   0           0                      0                    0   
4                   0           0                      0                    0   

   Auto Garage  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0            0                0          0           0           0       0   
1            0                0          0           0           0       0   
2            0                0          0           0           0       0   
3            0                0          0           0           0       0   
4            0                0          0           0           0       0   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0     0    0               0                 0                 0   
1     0    0               0                 0                 0   
2     0    0               0                 0                 0   
3     0    0               0                 0                 0   
4     0    0               0                 0                 0   

   Basketball Stadium  Bath House  Beach  Beach Bar  Bed & Breakfast  \
0                   0           0      0          0                0   
1                   0           0      0          0                0   
2                   0           0      0          0                0   
3                   0           0      0          0                0   
4                   0           0      0          0                0   

   Beer Bar  Beer Garden  Beer Store  Big Box Store  Bike Rental / Bike Share  \
0         0            0           0              0                         0   
1         0            0           0              0                         0   
2         0            0           0              0                         0   
3         0            0           0              0                         0   
4         0            0       

In [25]:
NY_onehot.shape

(9822, 430)

In [26]:
NY_grouped = NY_onehot.groupby('Neighborhood').mean().reset_index()
NY_grouped

Neighborhood  Accessories Store  Adult Boutique  \
0                     Allerton           0.000000        0.000000   
1                     Annadale           0.000000        0.000000   
2                Arden Heights           0.000000        0.000000   
3                    Arlington           0.000000        0.000000   
4                     Arrochar           0.000000        0.000000   
5                      Arverne           0.000000        0.000000   
6                      Astoria           0.000000        0.000000   
7              Astoria Heights           0.000000        0.000000   
8                   Auburndale           0.000000        0.000000   
9                   Bath Beach           0.000000        0.000000   
10           Battery Park City           0.000000        0.000000   
11                   Bay Ridge           0.000000        0.000000   
12                 Bay Terrace           0.020833        0.000000   
13                  Baychester           0.000000        0.000000   
14                     Bayside           0.000000        0.000000   
15                   Bayswater           0.000000        0.000000   
16                Bedford Park           0.000000        0.000000   
17          Bedford Stuyvesant           0.000000        0.000000   
18                  Beechhurst           0.000000        0.000000   
19                    Bellaire           0.000000        0.000000   
20                Belle Harbor           0.000000        0.000000   
21                   Bellerose           0.000000        0.000000   
22                     Belmont           0.000000        0.000000   
23                 Bensonhurst           0.000000        0.000000   
24                Bergen Beach           0.000000        0.000000   
25                  Blissville           0.000000        0.000000   
26                  Bloomfield           0.000000        0.000000   
27                 Boerum Hill           0.000000        0.000000   
28                Borough Park           0.000000        0.000000   
29                Breezy Point           0.000000        0.000000   
30                   Briarwood           0.000000        0.000000   
31              Brighton Beach           0.000000        0.000000   
32               Broad Channel           0.000000        0.000000   
33           Broadway Junction           0.000000        0.000000   
34                   Bronxdale           0.000000        0.000000   
35            Brooklyn Heights           0.000000        0.000000   
36                  Brookville           0.000000        0.000000   
37                 Brownsville           0.000000        0.000000   
38                  Bulls Head           0.000000        0.000000   
39                    Bushwick           0.000000        0.000000   
40                Butler Manor           0.000000        0.000000   
41             Cambria Heights           0.000000        0.000000   
42                    Canarsie           0.000000        0.000000   
43               Carnegie Hill           0.000000        0.000000   
44             Carroll Gardens           0.000000        0.000000   
45                 Castle Hill           0.000000        0.000000   
46           Castleton Corners           0.000000        0.000000   
47              Central Harlem           0.000000        0.000000   
48                  Charleston           0.000000        0.000000   
49                     Chelsea           0.000000        0.000000   
50                   Chinatown           0.000000        0.000000   
51                 City Island           0.000000        0.000000   
52                   City Line           0.000000        0.000000   
53                Civic Center           0.000000        0.000000   
54           Claremont Village           0.000000        0.000000   
55                Clason Point           0.000000        0.000000   
56                     Clifton           0.000000        0.000000   
57              

In [27]:
NY_grouped.shape

(301, 430)

In [25]:
out_path = "C:\\Users\\Mirzana\\IBM\\NY_grouped.xlsx"

writer = pd.ExcelWriter(out_path , engine='xlsxwriter')
NY_grouped.to_excel(writer, sheet_name='Sheet1')
writer.save()